CREACIÓ DE LES CLAUS: 
L'Alice crea una base bona, és a dir, una base suficientment ortogonal, i una base dolenta.
La base bona passarà a ser la clau privada de l'Alice, mentre que la base dolenta es publicarà com a clau pública.

In [ ]:
import time
# 1. Creem una base bona

# Determinem la dimensió de la base i el paràmetre k:
n = 3
k = 0.00001

# Fixem un parametre d i escollim aleatòriament les coordenades dels vectors entre -d i d:
d = 20
V =[]
for i in range (0,n):
    vi = []
    for j in range (0,n):
        vr = ZZ.random_element(-d,d+1)
        vi.append(vr)
    V.append(vi)
V = Matrix(V)

# 2. Comprovem que és una bona base

# Calculem el det(L) i comprovem que és diferent de 0:
det = V.det().abs()
print("det(L) = " + str(det))
if det == 0:
    print("Els vectors generats no formen una base!")
    
else:
    # Calculem el coeficient de Hadamard:
    N = 1
    for i in range (0,n):
        norma = RR(V.row(i).norm())
        N = N*norma
    H = (det/N)^(1/n)

    #Comprovem que és proper a 1:
    if H > k:
        print("La base V és bona, ja que té un quocient de Hadamard = " + str(H) + ".")
        print("La clau privada de l'Alice és la base:")
        print(V)

        # 3. Creem una base dolenta
        
        U = identity_matrix(n) # U = id
        W = Matrix(n)
        W = U * V # W = U*V = V

        # Calculem el seu quocient de Hadamard:
        det = W.det().abs()
        N = 1
        for i in range (0,n):
            norma = RR(W.row(i).norm())
            N = N*norma
        H = RR((det/N)^(1/n))

        # Multipliquem per matrius elementals fins a trobar una base dolenta:
        while H > k:
            # Multipliquem per una matriu elemental:
            Z = identity_matrix(n)
            i = ZZ.random_element(0, n)
            j = ZZ.random_element(0, n)
            while j == i:
                j = ZZ.random_element(0, n)
            a = ZZ.random_element(-1000, 1000)
            Z.add_multiple_of_row(i, j, a)
            U = U*Z
            W = U*V
            # Calculem el seu quocient de Hadamard:
            det = W.det().abs()
            N = 1
            for i in range (0,n):
                norma = RR(W.row(i).norm())
                N = N*norma
            H = RR((det/N)^(1/n))
        detU = U.det()
        print("U = " + str(U))
        print("detU = " + str(detU))
        

        # La base resoltant serà una base dolenta ja que ha sortit del while.
        print("La base W és dolenta, ja que té un quocient de Hadamard = " + str(H) + ".")
        print("La clau pública és la base:")
        print(W)

    else: 
        print("La base és dolenta!")
        

PROCÉS DE XIFRATGE: En Bob vol enviar un missatge secret a l'Alice. Per fer-ho ha d'escollir un vector aleatori r i calcular el text xifrat e = m*W + r.

In [ ]:
# 1. En Bob introdueix el missatge a xifrar
m = vector([-46, 78, -100])

# 2. Tria un vector aleatori r petit
r =[]
delta = 2
for i in range (0,n):
    rr = ZZ.random_element(-delta, delta)
    r.append(rr)
r = vector(r)
print("r = " + str(r))
    
# 3. Calcula el text xifrat e
e = zero_vector(n)
e = m*W + r
print("El text xifrat del Bob és: " + str(e))


PROCÉS DE DESXIFRATGE: Per desencriptar el text xifrat e, l'Alice fa ús de l'algorisme de Babai sobre la seva clau privada.

In [ ]:
# 1. L'Alice expressa el text xifrat e en funció de la base privada
Inv = V.inverse()
T = vector(e*Inv)
print("T = " + str(T))

# 2. L'Alice aplica l'algorisme de Babai sobre la seva clau privada
a = zero_vector(n)
v = zero_vector(n)
for i in range(0,n):
    a[i] = round(T[i]) # Arrodonim els coeficients a l'enter més pròxim 
    print("a(i) = " + str(a[i]))
    v = v + a[i]*V.row(i) # El vector resultant és mW
    
print("v = " + str(v))

# 3. Ara multiplica per W^-1 i recupera m
msol = v*W.inverse()
print("m = " + str(msol))

PROVA DE SEGURETAT: L'Eve coneix el text xifrat i la clau pública. Amb aquestes dades vol intentar desxifrar e aplicant l'algorisme de Babai a la base pública.

In [ ]:
# 1. L'Eve expressa el text xifrat e en funció de la base pública
InvE = W.inverse()
TE = e*InvE
print("TE = " + str(TE))

# 2. L'Eve aplica l'algorisme de Babai sobre la clau pública
aE = zero_vector(n)
vE = zero_vector(n)
for i in range(0,n):
    aE[i] = round(TE[i])
    print("aE(i) = " + str(aE[i]))
    vE = vE + aE[i]*W.row(i)
print("v = " + str(vE))

# 3. Ara multiplica per W^-1
msol = vE*W.inverse()
print("m' = " + str(msol))

COMPARACIÓ DE LES DUES CLAUS: Comparem les dues bases i l'efecte que ha tingut l'algorisme de Babai sobre elles.

In [ ]:
# COMPARACIÓ DE LES DUES CLAUS

error1 = e-v
error2 = e-vE
norm1 = RR(error1.norm())
norm2 = RR(error2.norm())
print("error1 = " + str(norm1))
print("error2 = " + str(norm2))


ALGORISME LLL: Per trencar el criptosistema i desencriptar e, l'Eve implementa l'algorisme LLL sobre la base W.

In [ ]:
MR = MatrixSpace(QQ,n,n)
v_LLL = copy(W)
k = 1

# Trobem la base ortogonal de Gram-Schmidt associada
v_GS = MR.matrix()
v_GS[0] = v_LLL.row(0)
for i in range (1,n):
    sumatori = zero_vector(QQ, n)
    for j in range (0,i):
        prod = v_LLL[i].dot_product(v_GS[j])
        norm = QQ(v_GS[j].norm()^2)
        mu = QQ(prod/norm)
        sumatori = sumatori + (mu*v_GS[j])
    v_GS[i] = v_LLL[i] - sumatori
    
v_GS[0] = v_LLL.row(0)

inici = time.time()
while k <= (n-1):
    for j in range (0,k):

        # Fem la reducció de mida
        prod = QQ(v_LLL[k].dot_product(v_GS[k-1-j]))
        norm = QQ((v_GS[k-1-j].norm())^2)
        mu = round(prod/norm)
        v_LLL[k] = v_LLL[k] - (mu*v_LLL[k-1-j])

        # Actualitzem la base de Gram-Schmidt
        v_GS[0] = v_LLL.row(0)
        for i in range (1,n):
            sumatori = zero_vector(QQ, n)
            for j in range (0,i):
                prod = v_LLL[i].dot_product(v_GS[j])
                norm = QQ(v_GS[j].norm()^2)
                mu = QQ(prod/norm)
                sumatori = sumatori + (mu*v_GS[j])
            v_GS[i] = v_LLL[i] - sumatori  
            
    normk = QQ(v_GS[k].norm()^2)
    prodk = QQ(v_LLL[k].dot_product(v_GS[k-1]))
    normkk = QQ(v_GS[k-1].norm()^2)
    muk = QQ(prodk/normkk)
    if normk >= (((3/4) - (muk^2))*normkk):
        k = k+1
    else:
        w = copy(v_LLL[k-1])
        v_LLL[k-1] = copy(v_LLL[k])
        v_LLL[k] = copy(w)
        k = max(k-1, 1)
        
        # Actualitzem la base de Gram-Schmidt
        v_GS[0] = v_LLL.row(0)
        for i in range (1,n):
            sumatori = zero_vector(QQ, n)
            for j in range (0,i):
                prod = v_LLL[i].dot_product(v_GS[j])
                norm = QQ(v_GS[j].norm()^2)
                mu = QQ(prod/norm)
                sumatori = sumatori + mu*v_GS[j]
            v_GS[i] = v_LLL[i] - sumatori
final = time.time()    
print("Temps d'execució de l'algorisme LLL : " + str(final - inici))

print("v_LLL = ")
print(v_LLL)

ATAC AL CRIPTOSISTEMA GGH AMB L'ALGORISME LLL: L'Eve aplica l'algorisme de Babai sobre la base LLL reduïda.

In [ ]:
# 1. L'Eve calcula la base LLL reduïda i comprova que és una bona base

# Calculem el seu quocient de Hadamard
det = v_LLL.det().abs()
N = 1
for i in range (0,n):
    norma = v_LLL.row(i).norm()
    N = N*norma
H = RR((det/N)^(1/n))
print("Quocient de Hadamard de la base LLL reduïda: " + str(H))

# 2. L'Eve expressa el text xifrat e en funció de la base LLL reduïda
InvE = v_LLL.inverse()
TE = e*InvE
print("TE = " + str(TE))

# 3. L'Eve aplica l'algorisme de Babai sobre la base LLL reduïda.
aE = zero_vector(n)
vE = zero_vector(n)
for i in range(0,n):
    aE[i] = round(TE[i]) 
    print("aE(i) = " + str(aE[i]))
    vE = vE + aE[i]*v_LLL.row(i)
print("vE = " + str(vE))

# Ara multiplica per W^-1
msol = vE*W.inverse()
print("m' = " + str(msol))